# Gradiente Descendente - Atv. 2

## Configurações e Classes Utilitárias

In [8]:
#%pip install numpy matplotlib IPython
#%matplotlib inline

Utilizaremos pra essa atividade alguns frameworks, os quais serão configurados conforme o código abaixo.

In [9]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

### Classe SSR

Definiremos a seguir a classe SSR (Sum of Squared Residuals), que agrupa os métodos de cálculo de gradiente, e de custo implementando e seguindo as seguintes fórmulas:

- Custo(SSR): $ \ J(m,b) =\sum^n_{i=1}(y_i-(mx_i+b))^2 $

- Gradiente de $ b \ $: $\ \dfrac{\partial J}{\partial b}=-2\sum^n_{i=1}(y_i-(mx_i+b)) $

- Gradiente de $ m \ $: $\ \dfrac{\partial J}{\partial m}=-2\sum^n_{i=1}x_i(y_i-(mx_i+b)) $

In [10]:
class SSR:
    def calculate_cost(X: np.array, y: np.array, m, b):
        y_pred = m * X + b
        residuals = y - y_pred
        return np.sum(residuals**2)

    def calculate_gradient_b(X, y, m, b):
        y_pred = m * X + b
        return -2 * np.sum(y - y_pred)

    def calculate_gradient_m(X, y, m, b):
        y_pred = m * X + b
        return -2 * np.sum(X * (y - y_pred))

### Animar com Slope Fixo

A classe FixedSlopePlot, tem como objetivo abstrair o processo de plotagem de gráficos, bem como a formatação do gráfico.\
Para o caso de Slope Fixado, a plotagem consiste em dois gráficos lado a lado, onde o gráfico do lado esquerdo mostra a curva de minimização de resíduo, e do lado direito, mostra a reta de ajuste ao dataset.

In [11]:
class FixedSlopePlot:
    def __init__(self, X, y, fixed_slope):
        self.X = X
        self.y = y
        self.fixed_slope = fixed_slope
        self.fig, (self.ax_left, self.ax_right) = plt.subplots(1, 2, figsize=(14, 6))

        self.point_cost, = self.ax_left.plot([], [], 'ro', markersize=10, zorder=5)
        self.line_tangent, = self.ax_left.plot([], [], 'g-', linewidth=2.5, label='Tangente')
        self.line_reg, = self.ax_right.plot([], [], 'r-', linewidth=3)

    def setup_background(self, history):
        # curva de custo
        b_values = [h[0] for h in history]
        buffer = 1.5
        b_range = np.linspace(min(b_values)-buffer, max(b_values)+buffer, 100)
        cost_curve = [SSR.calculate_cost(self.X, self.y, self.fixed_slope, b) for b in b_range]

        self.ax_left.plot(b_range, cost_curve, 'k--', alpha=0.4)
        self.ax_left.set_title("Minimização do Custo (Visualizando a Derivada)")
        self.ax_left.set_xlabel("Intercepto (b)")
        self.ax_left.set_ylabel("Custo (SSR)")
        self.ax_left.grid(True, linestyle=':', alpha=0.6)

        # reta de ajuste
        self.ax_right.scatter(self.X, self.y, color='blue', s=100)
        self.ax_right.set_xlim(min(self.X)-1, max(self.X)+1)
        self.ax_right.set_ylim(min(self.y)-1, max(self.y)+1)
        self.ax_right.set_title(f"Ajuste da Reta (Slope fixo: {self.fixed_slope})")
        self.ax_right.grid(True, linestyle=':', alpha=0.6)

    def create_animation(self, history):
        self.setup_background(history)

        def update(frame):
            b, cost, grad = history[frame]
            self.point_cost.set_data([b], [cost])

            # reta tangente
            x_tan = np.linspace(b - 1.5, b + 1.5, 10)
            y_tan = cost + grad * (x_tan - b)
            self.line_tangent.set_data(x_tan, y_tan)

            # atualiza reta de ajuste
            x_line = np.array([self.ax_right.get_xlim()[0], self.ax_right.get_xlim()[1]])
            y_line = self.fixed_slope * x_line + b
            self.line_reg.set_data(x_line, y_line)

            self.ax_right.legend([f"Intercept = {b:.4f}"], loc='upper left')

            return self.point_cost, self.line_tangent, self.line_reg

        plt.close()
        return FuncAnimation(self.fig, update, frames=len(history), interval=200, blit=True)

### Animar Regressão Completa

Podemos observar que ao otimizarmos dois parâmetros simultaneamente, o gráfico de minimização seria tridimensional, o que nesse contexto não é de importância, então a esta classe apenas mostra a animação centralizada da reta se ajustando melhor a cada iteração, ao dados.

In [12]:
class CompleteRegressionPlot:
    def __init__(self, X, y):
        self.X = X
        self.y = y
        self.fig, self.ax = plt.subplots(figsize=(8, 6))

        # Elementos Gráficos
        self.line_reg, = self.ax.plot([], [], 'r-', linewidth=3)
        self.scatter = self.ax.scatter(self.X, self.y, color='blue', s=100, label='Dados')

    def setup_background(self):
        self.ax.set_xlim(min(self.X)-1, max(self.X)+1)
        self.ax.set_ylim(min(self.y)-1, max(self.y)+1)
        self.ax.set_title("Regressão Completa (Otimizando m e b)")
        self.ax.grid(True, linestyle=':', alpha=0.6)

    def create_animation(self, history):
        self.setup_background()

        def update(frame):
            # Desempacota a tupla completa de 5 elementos
            m, b, cost, grad_m, grad_b = history[frame]

            # Atualiza Reta
            x_line = np.array([self.ax.get_xlim()[0], self.ax.get_xlim()[1]])
            y_line = m * x_line + b
            self.line_reg.set_data(x_line, y_line)

            # Atualiza Legenda
            self.ax.legend([f"Slope (m) = {m:.4f}\nIntercept (b) = {b:.4f}"], loc='upper left')

            return self.line_reg,

        plt.close()
        return FuncAnimation(self.fig, update, frames=len(history), interval=100, blit=True)

## Item A - Regressão Linear com Slope Fixado

Conforme o comando da atividade, para este exercício proposto, focaremos na otimzação apenas do intercept da função que se ajusta ao nosso da dataset.\
Reta essa que pode ser definida por: $ p(x)=mx+b$, onde:
- $p(x)$ é o valor previsto pra entrada $x$
- $ m $ é o slope
- $ b $ é o intercept

Nesse caso específico, o valor do slope já é conhecido, que equivale a 0.64, baseado nisso, a regressão deve seguir uma estrutura como:
- $p(x)=0.64x+b$\
onde $b$ seria o único parâmetro a ser otimizado.

In [13]:
def train_fixed_slope(X, y, fixed_slope, start_b, learning_rate=0.01, epochs=30):
    current_b = start_b
    history = []

    for _ in range(epochs):
        cost = SSR.calculate_cost(X, y, fixed_slope, current_b)
        grad = SSR.calculate_gradient_b(X, y, fixed_slope, current_b)

        history.append((current_b, cost, grad))

        current_b = current_b - (learning_rate * grad)

        # quebra se step size == 0
        if (learning_rate * grad) == 0:
            break

        step_size = learning_rate * grad
        old_b = current_b + step_size
        new_b = current_b
        print(f"| step_size={step_size:.6f} | old_intercept={old_b:.6f} | new_intercept={new_b:.6f} |")

    return history

In [14]:
# dataset
X_data = np.array([0.75, 2.5, 4.0 , 5])
y_data = np.array([1.5, 2.0, 4.0 , 4.5])

hist_fixed = train_fixed_slope(X_data, y_data, fixed_slope=0.64, start_b=0.0, learning_rate=0.01, epochs=50)

plot_A = FixedSlopePlot(X_data, y_data, fixed_slope=0.64)
anim_A = plot_A.create_animation(hist_fixed)
display(HTML(anim_A.to_jshtml()))

| step_size=-0.083200 | old_intercept=0.000000 | new_intercept=0.083200 |
| step_size=-0.076544 | old_intercept=0.083200 | new_intercept=0.159744 |
| step_size=-0.070420 | old_intercept=0.159744 | new_intercept=0.230164 |
| step_size=-0.064787 | old_intercept=0.230164 | new_intercept=0.294951 |
| step_size=-0.059604 | old_intercept=0.294951 | new_intercept=0.354555 |
| step_size=-0.054836 | old_intercept=0.354555 | new_intercept=0.409391 |
| step_size=-0.050449 | old_intercept=0.409391 | new_intercept=0.459840 |
| step_size=-0.046413 | old_intercept=0.459840 | new_intercept=0.506252 |
| step_size=-0.042700 | old_intercept=0.506252 | new_intercept=0.548952 |
| step_size=-0.039284 | old_intercept=0.548952 | new_intercept=0.588236 |
| step_size=-0.036141 | old_intercept=0.588236 | new_intercept=0.624377 |
| step_size=-0.033250 | old_intercept=0.624377 | new_intercept=0.657627 |
| step_size=-0.030590 | old_intercept=0.657627 | new_intercept=0.688217 |
| step_size=-0.028143 | old_intercept=

## Item B.1 - Regressão Linear Completa

Nesse caso fazemos a regressão linear completa, ou seja, ajustamos o slope $m$ e o intercept $b$ simultaneamente na equação:
$$ p(x)=mx+b $$

A função train_complete aplica o gradiente descendente nos dois parâmetros. A cada iteração ela:
- Calcula o custo (SSR) com os valores atuais de $m$ e $b$.
- Obtém os gradientes $\frac{\partial SSR}{\partial m}$ e $\frac{\partial SSR}{\partial b}$
- Atualiza os valores

In [15]:
def train_complete(X, y, start_m, start_b, learning_rate=0.01, epochs=30, include_final=True):
    current_m = start_m
    current_b = start_b
    history = []

    for _ in range(epochs):
        cost = SSR.calculate_cost(X, y, current_m, current_b)
        grad_m = SSR.calculate_gradient_m(X, y, current_m, current_b)
        grad_b = SSR.calculate_gradient_b(X, y, current_m, current_b)

        history.append((current_m, current_b, cost, grad_m, grad_b))

        current_m -= learning_rate * grad_m
        current_b -= learning_rate * grad_b

        step_size = learning_rate * grad_b
        old_b = current_b + step_size
        new_b = current_b
        print(f"| step_size={step_size:.6f} | old_intercept={old_b:.6f} | new_intercept={new_b:.6f} |")

    if include_final:
        cost = SSR.calculate_cost(X, y, current_m, current_b)
        grad_m = SSR.calculate_gradient_m(X, y, current_m, current_b)
        grad_b = SSR.calculate_gradient_b(X, y, current_m, current_b)
        history.append((current_m, current_b, cost, grad_m, grad_b))

    return history

Dessa forma conseguiremos realizar uma execução do treinamento completo (slope e intercept).

In [19]:
hist_full = train_complete(X_data, y_data, start_m=5.0, start_b=3.0, learning_rate=0.01, epochs=50)

plot_B = CompleteRegressionPlot(X_data, y_data)
anim_B = plot_B.create_animation(hist_full)
display(HTML(anim_B.to_jshtml()))

| step_size=1.225000 | old_intercept=3.000000 | new_intercept=1.775000 |
| step_size=-0.005819 | old_intercept=1.775000 | new_intercept=1.780819 |
| step_size=0.018617 | old_intercept=1.780819 | new_intercept=1.762202 |
| step_size=0.017827 | old_intercept=1.762202 | new_intercept=1.744376 |
| step_size=0.017549 | old_intercept=1.744376 | new_intercept=1.726827 |
| step_size=0.017265 | old_intercept=1.726827 | new_intercept=1.709562 |
| step_size=0.016986 | old_intercept=1.709562 | new_intercept=1.692576 |
| step_size=0.016712 | old_intercept=1.692576 | new_intercept=1.675864 |
| step_size=0.016442 | old_intercept=1.675864 | new_intercept=1.659422 |
| step_size=0.016176 | old_intercept=1.659422 | new_intercept=1.643246 |
| step_size=0.015915 | old_intercept=1.643246 | new_intercept=1.627331 |
| step_size=0.015658 | old_intercept=1.627331 | new_intercept=1.611673 |
| step_size=0.015405 | old_intercept=1.611673 | new_intercept=1.596268 |
| step_size=0.015156 | old_intercept=1.596268 | ne

## Item B.2 - Regressão Linear Completa (Gradiente Estocástico)